In [2]:
import pandas as pd
from netCDF4 import Dataset
import csv
import numpy as np
import datetime as dt
import os
import math

# ANSI escape sequences for colors
RED_FONT = "\033[31m"  # Red font color
BLUE_FONT = "\033[34m"  # Blue font color
GREEN_FONT = "\033[32m"  # Green font color
MAGENTA_FONT = "\033[35m"
RESET = "\033[0m"  # Reset colors to default

#-------------------------------FUNCTION START---------------------------------------------------------------#

# Define the Haversine distance function
def haversine_distance(coord1, coord2):
    # Radius of the Earth in meters
    R = 6371000  
    # Convert latitude and longitude from degrees to radians
    lon1, lat1 = np.radians(coord1)
    lon2, lat2 = np.radians(coord2)
    # Differences in coordinates
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    # Haversine formula
    a = np.sin(dlat / 2.0)**2 + np.cos(lat1) * np.cos(lat2) * np.sin(dlon / 2.0)**2
    c = 2 * np.arctan2(np.sqrt(a), np.sqrt(1 - a))
    distance = R * c  # Output distance in meters
    return distance


def find_closest_era5_point(ext_point, era5_coords):
    """
    Finds the closest point from a list of ERA5 coordinates to a given external point.

    Parameters:
    - ext_point: tuple, containing the longitude and latitude of the external point.
    - era5_coords_col: numpy array, containing tuples of longitude and latitude coordinates.

    Returns:
    - closest_coord: tuple, the closest ERA5 coordinate to the external point.
    - closest_index: int, index of the closest ERA5 coordinate.
    - min_distance: float, distance to the closest ERA5 coordinate.
    """
    min_distance = float('inf')
    closest_index = -1
    closest_coord = None

    # Calculate distances to each ERA5 coordinate
    for idx, era5_point in enumerate(era5_coords):
        distance = haversine_distance(ext_point, era5_point)
        #print(ext_point, era5_point)
        if distance < min_distance:
            min_distance = distance
            closest_index = idx
            closest_coord = era5_point
    return closest_coord, closest_index, min_distance

def delete_file(file_path):
    if os.path.exists(file_path):
        os.remove(file_path)
        print("Previous File deleted successfully.")
    else:
        print("File does not exist.")



#-------------------------------FUNCTION END---------------------------------------------------------------#
#----------------------------------------------------------------------------------------------------------#
#-------------------------------INPUT START---------------------------------------------------------------#
outtext_path = r"H:\Shadman\Isabel_2003_AtlanticModels\AtlanticAllForcing_2003\BnDEra5RadianWave2003Full.bcw"
### deleting the existing bcw file
delete_file(outtext_path)
print("============================================")

ds=Dataset(r"C:\Users\Shadman\Downloads\9f5774e35bf3ba365154b2b648409b7f.nc")

deflt3d_ref_time = dt.datetime.strptime('2001-01-01 00:00:00', '%Y-%m-%d %H:%M:%S')
era5_ref_time = dt.datetime.strptime('1970-01-01 00:00:00', '%Y-%m-%d %H:%M:%S')

### read the data from csv for the BnD cordinates
WaveBnD=pd.read_csv(r"D:\FinalCPBModel\Wave\Data\BnD\input\WaveBoundaryInfo_11Cor.csv")

# Define the start and end dates
start_date = '2003-01-01 00:00:00'
end_date = '2003-12-31 23:00:00'
timestamps = pd.date_range(start=start_date, end=end_date, freq='1H')

#-------------------------------INPUT END---------------------------------------------------------------#
#--------------------------------------------------------------------------------------------------------#
#-------------------------------PROCESS START---------------------------------------------------------------#


### extracting matching timestamp indices
era5_time=ds.variables['valid_time']

timestamps_from_era5_ref = np.array((timestamps - era5_ref_time) / pd.Timedelta(seconds=1))
timestamps_from_delft3d_ref = np.array((timestamps - deflt3d_ref_time) / pd.Timedelta(seconds=1))

matches = np.isin(era5_time, timestamps_from_era5_ref)
time_indices = np.where(matches)[0]

### creating the mesh for the era5 datap points.
era5_lon=np.array(ds.variables['longitude'][:].data)
era5_lat=np.array(ds.variables['latitude'][:].data)
#creating the meshgrid! Correct!
era5_lon_grid, era5_lat_grid = np.meshgrid(era5_lon, era5_lat)
era5_coords = np.column_stack((era5_lon_grid.ravel(), era5_lat_grid.ravel())) ### tuple has been created to iterate through them



### craeting the mesh for the BnD points

for i in range(len(WaveBnD)):
    ext_lon=np.array(WaveBnD['Lon_BnD'][i])
    ext_lat=np.array(WaveBnD['Lat_BnD'][i])
    ext_name=WaveBnD['Name'][i]
    ## creating the point to feed into the function
    ext_point = (ext_lon, ext_lat)

    
    ### extracting the closest lat lon point: era5 --> target
    era5_point, closest_index, min_distance = find_closest_era5_point(ext_point, era5_coords)
    print(f"BnD_Cor: {ext_point}, ERA5_Lon: {era5_point[0]}, ERA5_Lat: {era5_point[1]}, Index: {closest_index}, Distance: {np.round(min_distance/1000,2)} km")

    ##### Finding the index of this lat, lon from the era5 dataset
    lon_index = np.where(era5_lon == era5_point[0])[0]
    lat_index = np.where(era5_lat == era5_point[1])[0]

    print(lon_index,lat_index)
    print(era5_lon[lon_index],era5_lat[lat_index])


    c=0

    list_temp=[]
    for t in time_indices:

        ### data extraction
        time=timestamps_from_delft3d_ref[c]/60 ### hours converted into minutes from reference time
        
        ############################################ Missing Data Alert: Setting up replacement for Hs data ################################
        hs=np.round(ds.variables['swh'][t,lat_index,lon_index][0][0],4) #swh(time, latitude, longitude) [0][0] is used to extract the value only/
        if np.ma.is_masked(hs):
            print(f"{RED_FONT}Alert!!!: Hs data missing: BnD {ext_name}; Replaced with 1.0m{RESET}")
            hs=1.0 #### replaced with 1.0
            
        ############################################ Missing Data Alert: Setting up replacement for Period data ###########################
        per=np.round(ds.variables['pp1d'][t,lat_index,lon_index][0][0],4)
        if np.ma.is_masked(per):
            print(f"{BLUE_FONT}Alert!!!: per data missing: BnD {ext_name}; Replaced with 15.0sec{RESET}")
            per=15 #### replaced with 15.0
        
        ############################################ Temporary: All direction set to 0 ###################################################
        ############################################ Convert Degree ----> Radians #######################################################
        dir=np.round(ds.variables['mwd'][t,lat_index,lon_index][0][0],4)
        dir=dir* (math.pi / 180)
        if np.ma.is_masked(dir):
            print(f"{GREEN_FONT}Alert!!!: per data missing: BnD {ext_name}; Replaced with 0.00degree{RESET}")
            dir=0.0 #### replaced with 15.0
        # else:
            # dir=0
        
        ############################################ Temporary: All spr set to 4 #########################################################
        spr=np.round(ds.variables['wdw'][t,lat_index,lon_index][0][0],4)

        if np.ma.is_masked(spr):
            print(f"{MAGENTA_FONT}Alert!!!: per data missing: BnD {ext_name}; Replaced with 2.0{RESET}")
            spr=2.0 #### replaced with 15.0
        else:
            spr=4.0


        list_temp.append([time,hs,per,dir,spr])

        c=c+1
        
    df_temp = pd.DataFrame(list_temp).to_string(index=False, header=None)
    #print(df_temp)

    # Correcting the variable error and rewriting the file
    with open(outtext_path, 'a') as file:
        file.write("location             '{}'\n".format(ext_name)) # the boundary name is written here
        file.write("time-function        'non-equidistant'\n")
        file.write("reference-time       20010101\n")
        file.write("time-unit            'minutes'\n")
        file.write("interpolation        'linear'\n")
        file.write("parameter            'time'               unit '[min]'\n")
        file.write("parameter            'WaveHeight'         unit '[m]'\n")
        file.write("parameter            'Period'             unit '[s]'\n")
        file.write("parameter            'Direction'          unit '[N^o]'\n")
        file.write("parameter            'DirSpreading'       unit '[-]'\n")
        file.write(df_temp)  # Append the dataframe text
        file.write("\n")
        file.write("\n")
    

    print("============================================")
    











### need to save the extracted data as a row in a dataframe. export it if you are writing a seperate program.
############################################################################################################################################
### the first value of the dataframe will be in minutes from the delft3d reference time.
### using this, we will write out the output values as text. This can be a seperate program!

Previous File deleted successfully.
BnD_Cor: (array(-98.6238), array(13.8354)), ERA5_Lon: -98.5, ERA5_Lat: 14.0, Index: 15369, Distance: 22.66 km
[5] [92]
[-98.5] [14.]
BnD_Cor: (array(-96.3712), array(13.8335)), ERA5_Lon: -96.5, ERA5_Lat: 14.0, Index: 15373, Distance: 23.15 km
[9] [92]
[-96.5] [14.]
BnD_Cor: (array(-94.1261), array(13.8364)), ERA5_Lon: -94.0, ERA5_Lat: 14.0, Index: 15378, Distance: 22.72 km
[14] [92]
[-94.] [14.]
BnD_Cor: (array(-91.879), array(13.8374)), ERA5_Lon: -92.0, ERA5_Lat: 14.0, Index: 15382, Distance: 22.3 km
[18] [92]
[-92.] [14.]
BnD_Cor: (array(-90.4457), array(13.8365)), ERA5_Lon: -90.5, ERA5_Lat: 14.0, Index: 15385, Distance: 19.1 km
[21] [92]
[-90.5] [14.]
Alert!!!: Hs data missing: BnD South05; Replaced with 1.0m
Alert!!!: per data missing: BnD South05; Replaced with 15.0sec
Alert!!!: per data missing: BnD South05; Replaced with 0.00degree
Alert!!!: per data missing: BnD South05; Replaced with 2.0
Alert!!!: Hs data missing: BnD South05; Replaced with 

In [13]:
timestamps_from_delft3d_ref

array([3.155328e+08, 3.155364e+08, 3.155400e+08, ..., 3.470580e+08,
       3.470616e+08, 3.470652e+08])

In [14]:
timestamps_from_era5_ref

array([1.2938400e+09, 1.2938436e+09, 1.2938472e+09, ..., 1.3253652e+09,
       1.3253688e+09, 1.3253724e+09])